# 🚀 NTv3 Quickstart — Pre-trained and Post-trained models

This notebook demonstrates how to run **quick inference** with both the pre- and post-trained NTv3 checkpoints:

- **Pre-trained (MLM-focused):** `InstaDeepAI/NTv3_8M_pre`, `InstaDeepAI/NTv3_100M_pre`, `InstaDeepAI/NTv3_650M_pre`
- **Post-trained (functional tracks and genome annotation):** `InstaDeepAI/NTv3_100M_pos`, `InstaDeepAI/NTv3_650M_pos`

We show how to:

1. Load tokenizers + models
2. Run a forward pass on a DNA sequence window
3. Inspect key outputs

> 📝 **Note for Google Colab users:** This notebook is compatible with Colab! For faster inference, make sure to enable GPU: Runtime → Change runtime type → GPU (T4 or better recommended).

## 0) 📦 Imports + setup

In [ ]:
!pip -q install "transformers>=4.40" "huggingface_hub>=0.23" safetensors torch numpy

In [3]:
import os
import torch
import numpy as np

from transformers import AutoConfig, AutoModel, AutoTokenizer, AutoModelForMaskedLM

# Optional: if the model is gated/private, set HF_TOKEN to a PERSONAL token (hf_...)
HF_TOKEN = os.getenv("HF_TOKEN", None)

# -----------------------------
# Device
# -----------------------------
device = "cuda" if torch.cuda.is_available() else "cpu"
print("device:", device)

# Choose dtype (bf16 if supported; else fp16 on GPU; else fp32)
if device == "cuda":
    major, minor = torch.cuda.get_device_capability(0)
    torch_dtype = torch.bfloat16 if major >= 8 else torch.float16
else:
    torch_dtype = torch.float32

print("torch_dtype:", torch_dtype)

device: cpu
torch_dtype: torch.float32


## 1) 🎯 Pre-trained checkpoint (MLM-focused)

This shows the simplest usage: load model + tokenizer, then run a forward pass.

Expected output:
- `logits`: masked language modeling logits

In [ ]:
pretrained_model_name = "InstaDeepAI/NTv3_8M_pre"

# Load tokenizer/model
tok_pre = AutoTokenizer.from_pretrained(pretrained_model_name, trust_remote_code=True)
model_pre = AutoModelForMaskedLM.from_pretrained(pretrained_model_name, trust_remote_code=True)

# Example: human sequence
seqs = ["ATCGNATCG", "ACGT"]
batch = tok_pre(seqs, add_special_tokens=False, padding=True, pad_to_multiple_of=128, return_tensors="pt")
out = model_pre(**batch, output_hidden_states=True, output_attentions=True)

print(out.logits.shape)       # (B, L, V = 11)
print(len(out.hidden_states)) # convs + transformers + deconvs
print(len(out.attentions))

# Access MLM logits
mlm_logits = out["logits"]
print("MLM logits shape:", tuple(mlm_logits.shape))

tokenizer_config.json:   0%|          | 0.00/1.48k [00:00<?, ?B/s]

tokenization_ntv3.py:   0%|          | 0.00/12.0k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/InstaDeepAI/ntv3_base_model:
- tokenization_ntv3.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


vocab.json:   0%|          | 0.00/138 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/149 [00:00<?, ?B/s]

...

A new version of the following files was downloaded from https://huggingface.co/InstaDeepAI/ntv3_base_model:
- configuration_ntv3.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


modeling_ntv3_base.py:   0%|          | 0.00/33.9k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/InstaDeepAI/ntv3_base_model:
- modeling_ntv3_base.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


model.safetensors:   0%|          | 0.00/30.8M [00:00<?, ?B/s]

torch.Size([2, 128, 11])
16
2
MLM logits shape: (2, 128, 11)


## 2) 🧠 Post-trained checkpoint (task heads: BigWig + BED)

Post-trained checkpoints add task-specific heads for functional track prediction and genome annotation.

In particular:
- `species_tokenizer` is used to tokenize a species condition like `"human"`
- `species_ids` passes the species tokens to the model

Expected outputs:
- `bigwig_tracks_logits`: functional track predictions
- `bed_tracks_logits`: genome annotation predictions
- `logits`: masked language modeling logits

In [9]:
# Inspect config and supported species
post_trained_model_name = "InstaDeepAI/NTv3_100M_pos"

cfg_post = AutoConfig.from_pretrained(post_trained_model_name, trust_remote_code=True)

species = "TO BE DONE"
print("Model supported species:", species)

Model supported species: TO BE DONE


In [ ]:
tok_post = AutoTokenizer.from_pretrained(post_trained_model_name, trust_remote_code=True)
cond_tok_post = AutoTokenizer.from_pretrained(post_trained_model_name, subfolder='species_tokenizer', trust_remote_code=True)
model_post = AutoModel.from_pretrained(post_trained_model_name, trust_remote_code=True)

# Prepare inputs
batch = tok_post(["ATCGNATCG", "ACGT"], add_special_tokens=False, padding=True, pad_to_multiple_of=128, return_tensors="pt")

# Condition tokens (e.g., species)
species = 'human'
species_ids = cond_tok_post([species] * len(batch['input_ids']), add_special_tokens=False, return_tensors='pt')

# Forward pass
out = model_post(
    input_ids=batch["input_ids"],
    species_ids=species_ids['input_ids'],
    return_dict=True
)

# 7k human tracks over 37.5 % center region of the input sequence
print("bigwig_tracks_logits:", tuple(out["bigwig_tracks_logits"].shape))
# Location of 21 genomic elements over 37.5 % center region of the input sequence
print("bed_tracks_logits:", tuple(out["bed_tracks_logits"].shape))
# Language model logits for whole sequence over vocabulary
print("language model logits:", tuple(out["logits"].shape))


torch.Size([1, 768, 7362])
torch.Size([1, 768, 21, 2])
torch.Size([1, 2048, 11])
